In [1]:
from pyspark.sql.readwriter import DataFrameReader
from pyspark.sql import SparkSession
import os


def get_dataframe_reader() -> DataFrameReader:
  """ Learn more: https://spark.apache.org/docs/latest/sql-data-sources-jdbc.html """

  env = os.environ.copy()
  host = env.get('NASDAQ_DATA_LINK_BASE_DOMAIN', 'data.nasdaq.com')
  url = f'jdbc:trino://{host}:443/main/huron'
  user = env['NASDAQ_DATA_LINK_API_KEY']

  spark = SparkSession.builder.appName("DataLink Spark DEMO").getOrCreate()
  dfr = spark.read \
    .format("jdbc") \
    .option("driver", "io.trino.jdbc.TrinoDriver") \
    .option("url", url) \
    .option("user", user)

  return dfr

In [2]:
# Learn more: https://data.nasdaq.com/databases/RTAT/documentation?anchor=retail-trading-activity-tracker-daily-top-10-free-ndaq-rtat10-
retail_activity = get_dataframe_reader().option("dbtable", "ndaq_rtat10").load()
retail_activity.show(10)

+---+----------+------+--------+---------+
| id|      date|ticker|activity|sentiment|
+---+----------+------+--------+---------+
|  1|2021-11-01|  TSLA|  0.0986|        3|
|  2|2021-11-01|   AMD|  0.0286|        1|
|  3|2021-11-01|  AAPL|  0.0274|       -1|
|  4|2021-11-01|  LCID|  0.0267|       -1|
|  5|2021-11-01|    FB|  0.0197|        3|
|  6|2021-11-01|  BTTX|  0.0172|        3|
|  7|2021-11-01|   SPY|  0.0156|        5|
|  8|2021-11-01|  NVDA|  0.0155|        4|
|  9|2021-11-01|   QQQ|   0.014|        2|
| 10|2021-11-01|  MSFT|  0.0138|        5|
+---+----------+------+--------+---------+
only showing top 10 rows



In [3]:
# Learn more: https://data.nasdaq.com/databases/ZHDM/documentation?anchor=historical-daily-maintenance-zacks-hdm-
corp_actions = get_dataframe_reader().option("dbtable", "zacks_hdm").load()
corp_actions.show(10)

+--------+-----------+--------+------+-----------------+---------------+------+------------+----------+----------+
|      id|action_type|m_ticker|status|per_end_month_nbr|      comp_name|ticker|  change_txt|   ex_date| proc_date|
+--------+-----------+--------+------+-----------------+---------------+------+------------+----------+----------+
|60791215|          5|    ENDP|     1|               12|  ENDO INTL PLC|  ENDP|       ENDPQ|      null|2022-08-26|
|60791216|          6|    NTRZ|     1|               12|  RICEBRAN TECH|  RIBT|      0.1000|2022-08-26|2022-08-26|
|60791217|          6|    CAPN|     1|               12|SOLENO THERPTCS|  SLNO|      0.0667|2022-08-26|2022-08-26|
|60791218|          6|    AZRX|     1|               12| FIRST WAVE BIO|  FWBI|      0.0333|2022-08-26|2022-08-26|
|60791219|          2|    PRIS|     1|               12|PROMOTORA DE IN| PRISY|  D-DELISTED|2022-08-26|2022-08-26|
|60791220|          2|    FST3|     1|               12|    FAST ACQ CP|   FST|L

In [4]:
sql = """
SELECT
    r.activity,
    r.sentiment,
    z.*
FROM
    ndaq_rtat10 r
        INNER JOIN
    zacks_hdm z ON z.ticker = r.ticker AND z.ex_date = r.date
"""
joined = get_dataframe_reader().option("query", sql).load()
joined.show(10)

+--------+---------+--------+-----------+--------+------+-----------------+--------------+------+----------+----------+----------+
|activity|sentiment|      id|action_type|m_ticker|status|per_end_month_nbr|     comp_name|ticker|change_txt|   ex_date| proc_date|
+--------+---------+--------+-----------+--------+------+-----------------+--------------+------+----------+----------+----------+
|  0.0526|        5|60791231|          6|    TSLA|     1|               12|     TESLA INC|  TSLA|    3.0000|2022-08-25|2022-08-25|
|  0.0122|        8|60791549|          6|    GOOG|     1|               12|ALPHABET INC-A| GOOGL|   20.0000|2022-07-18|2022-07-18|
|  0.0732|        4|60791898|          6|    AMZN|     1|               12|AMAZON.COM INC|  AMZN|   20.0000|2022-06-06|2022-06-06|
|   0.021|        6|60793090|          6|    TQQQ|     1|               12|   PRO-ULT QQQ|  TQQQ|    2.0000|2022-01-13|2022-01-13|
|  0.0252|        3|60795230|          6|    NVDA|     1|                1|   NVIDI